# Case3-1: マジックコマンドを自作してみる  
Create own magic command

In [1]:
import functools
from IPython.core.magic import register_line_magic, register_cell_magic
from IPython.display import IFrame
import pandas as pd
import yaml
import ast
from io import StringIO

## line magic

In [2]:
@register_line_magic
def ms(code):
    url = "https://www.morningstar.co.jp/StockInfo/info/snap/{0}".format(code)
    print(url)
    return IFrame(url, "100%", 600)

In [3]:
%ms 7974

https://www.morningstar.co.jp/StockInfo/info/snap/7974


## cell magic

In [4]:
@register_cell_magic
def csv(line, cell):
    sio = StringIO(cell)
    if line:
        options = dict(ast.literal_eval(line))
        return pd.read_csv(sio, **options)
    else:
        return pd.read_csv(sio)

In [5]:
@register_cell_magic
def yml(line, cell):
    sio = StringIO(cell)
    return pd.DataFrame(yaml.load(sio))

In [6]:
@register_cell_magic
def json(line, cell):
    sio = StringIO(cell)
    return pd.read_json(sio)

### csv形式のデータをDataFrameに変換  
convert csv data into DataFrame

pandas.read_html()では読み込めないがコピペすることでDataFrameとして取り込める  
cannot read data by pdandas.read_html(), but can fetch data as DataFrame by copy&paste

In [7]:
%%csv {'sep': '\t', 'header': None}
始値	26,910	（09/13 09:00）
高値	27,080	（09/13 09:05）
安値	25,590	（09/13 14:52）
出来高（株）	6,017,700	（09/13 15:00）
前日終値	26,690	（09/12）
年初来高値	32,700	（2016/7/19）
年初来安値	13,360	（2016/6/28）
発行済株式数（千株）	141,669	 

0          1              2
0          始値     26,910  （09/13 09:00）
1          高値     27,080  （09/13 09:05）
2          安値     25,590  （09/13 14:52）
3      出来高（株）  6,017,700  （09/13 15:00）
4        前日終値     26,690        （09/12）
5       年初来高値     32,700    （2016/7/19）
6       年初来安値     13,360    （2016/6/28）
7  発行済株式数（千株）    141,669

\_ に直前の結果が格納されている  
store the previous output in \_

In [8]:
df = _

In [9]:
df.head()

0          1              2
0      始値     26,910  （09/13 09:00）
1      高値     27,080  （09/13 09:05）
2      安値     25,590  （09/13 14:52）
3  出来高（株）  6,017,700  （09/13 15:00）
4    前日終値     26,690        （09/12）

### json形式のデータをDataFrameに変換  
Covert json type data into DataFrame

> * json data  
> https://www.google.com/finance/info?q=NASDAQ%3aGOOG

In [10]:
%%json
[ { "id": "304466804484872" ,"t" : "GOOG" ,"e" : "NASDAQ" ,"l" : "767.05" ,"l_fix" : "767.05" ,"l_cur" : "767.05" ,"s": "1" ,"ltt":"4:00PM EDT" ,"lt" : "Aug 31, 4:00PM EDT" ,"lt_dts" : "2016-08-31T16:00:02Z" ,"c" : "0.00" ,"c_fix" : "0.00" ,"cp" : "0.00" ,"cp_fix" : "0.00" ,"ccol" : "chb" ,"pcls_fix" : "767.05" ,"el": "767.89" ,"el_fix": "767.89" ,"el_cur": "767.89" ,"elt" : "Sep 1, 9:24AM EDT" ,"ec" : "+0.84" ,"ec_fix" : "0.84" ,"ecp" : "0.11" ,"ecp_fix" : "0.11" ,"eccol" : "chg" ,"div" : "" ,"yld" : "" } ]

c  c_fix ccol  cp  cp_fix div       e    ec  ec_fix eccol ...        l  \
0  0      0  chb   0       0      NASDAQ  0.84    0.84   chg ...   767.05   

    l_cur   l_fix                  lt                lt_dts         ltt  \
0  767.05  767.05  Aug 31, 4:00PM EDT  2016-08-31T16:00:02Z  4:00PM EDT   

   pcls_fix  s     t  yld  
0    767.05  1  GOOG       

[1 rows x 27 columns]

In [11]:
_.T

0
c                            0
c_fix                        0
ccol                       chb
cp                           0
cp_fix                       0
div                           
e                       NASDAQ
ec                        0.84
ec_fix                    0.84
eccol                      chg
ecp                       0.11
ecp_fix                   0.11
el                      767.89
el_cur                  767.89
el_fix                  767.89
elt          Sep 1, 9:24AM EDT
id             304466804484872
l                       767.05
l_cur                   767.05
l_fix                   767.05
lt          Aug 31, 4:00PM EDT
lt_dts    2016-08-31T16:00:02Z
ltt                 4:00PM EDT
pcls_fix                767.05
s                            1
t                         GOOG
yld

### yaml形式のデータをDataFrameに変換  
convert yaml type data into DataFrame

yaml data at [Case2-3](Case2-3.ipynb)

In [12]:
%%yml
1970-01-01:
  date: 1970-01-01
  week: 木
  week_en: Thursday
  name: 元日
  name_en: "New Year's Day"

1970-01-15:
  date: 1970-01-15
  week: 木
  week_en: Thursday
  name: 成人の日
  name_en: "Coming of Age Day"

1970-02-11:
  date: 1970-02-11
  week: 水
  week_en: Wednesday
  name: 建国記念の日
  name_en: "National Foundation Day"

1970-01-01         1970-01-15               1970-02-11
date         1970-01-01         1970-01-15               1970-02-11
name                 元日               成人の日                   建国記念の日
name_en  New Year's Day  Coming of Age Day  National Foundation Day
week                  木                  木                        水
week_en        Thursday           Thursday                Wednesday

In [13]:
_.T

date    name                  name_en week    week_en
1970-01-01  1970-01-01      元日           New Year's Day    木   Thursday
1970-01-15  1970-01-15    成人の日        Coming of Age Day    木   Thursday
1970-02-11  1970-02-11  建国記念の日  National Foundation Day    水  Wednesday